In [ ]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix,roc_curve, auc

from keras.models import Sequential
from keras.layers import Conv2D, Lambda, MaxPooling2D # convolution layers
from keras.layers import Dense, Dropout, Flatten # core layers

from keras.layers.normalization import BatchNormalization

from keras.preprocessing.image import ImageDataGenerator

from keras.utils.np_utils import to_categorical

#from keras.datasets import mnist
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import seaborn as sns
import matplotlib.pyplot as plt
# import warnings
import warnings
# filter warnings
warnings.filterwarnings('ignore')


import os
print(os.listdir("../input"))

data = pd.read_csv("../input/500lukveri/data.csv")
print(data.shape)
data.head()

X=data.iloc[0:, 1:-1]
y=data.iloc[:,-1]

from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
X = SelectKBest(chi2, k=100).fit_transform(X, y)

"""dizi2=np.zeros([7622,51])
print(dizi2.shape)

X = np.concatenate((X, dizi2), axis=1)
print(X.shape)
"""

X[X == 0] = 255
X[X == 1] = 0


X=pd.DataFrame(X)
print(X.shape)
X.head()

img = X.iloc[39].as_matrix()
img = img.reshape((10,10))
plt.imshow(img,cmap='gray')
plt.axis("off")
plt.show()

X = X.values.reshape(-1,10,10,1)
print("x_train shape: ",X.shape)

X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.30, random_state=123)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=123)
print("x_train shape", X_train.shape)
print("x_val shape", X_val.shape)
print("x_test shape", X_test.shape)
print("y_train shape", y_train.shape)
print("y_val shape", y_val.shape)
print("y_test shape", y_test.shape)

Y_train = to_categorical(y_train, num_classes=2)
Y_val = to_categorical(y_val, num_classes=2)
Y_test = to_categorical(y_test, num_classes=2)
print(Y_train.shape)
print(Y_val.shape)
print(Y_test.shape)

from sklearn.metrics import confusion_matrix
import itertools
from keras.layers import LeakyReLU
from keras.utils.np_utils import to_categorical # convert to one-hot-encoding
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPool2D
from keras.optimizers import RMSprop,Adam,Nadam
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import ReduceLROnPlateau,ModelCheckpoint
import tensorflow as tf
keras = tf.keras  

from tensorflow.keras import layers
from tensorflow.keras import initializers
#initializer = tf.keras.initializers.RandomUniform(minval=0., maxval=1.)

from keras.layers import Add, Input, Activation, Conv2D, MaxPooling2D, GlobalAveragePooling2D, Flatten, Dense, Reshape, Multiply
from keras.models import Model
from keras.initializers import he_normal, glorot_uniform

def residual_block(input_tensor, filters, strides=(1, 1), downsample=False):
    shortcut = input_tensor
    x = Conv2D(filters=filters, kernel_size=(3, 3), strides=strides, padding='same', kernel_initializer=glorot_uniform())(input_tensor)
    x = Activation('relu')(x)
    x = Conv2D(filters=filters, kernel_size=(3, 3), padding='same', kernel_initializer=glorot_uniform())(x)

    if downsample:
        shortcut = Conv2D(filters=filters, kernel_size=(1, 1), strides=strides, padding='same', kernel_initializer=glorot_uniform())(input_tensor)

    x = Add()([shortcut, x])
    x = Activation('relu')(x)
    return x

def attention_block(input_tensor, filters):
    # Compression Part
    x = Conv2D(filters=filters, kernel_size=(1, 1), strides=(1, 1), padding='same', kernel_initializer=glorot_uniform())(input_tensor)
    x = Activation('relu')(x)
    x = Conv2D(filters=filters, kernel_size=(1, 1), strides=(1, 1), padding='same', kernel_initializer=glorot_uniform())(x)

    # Excitation Part
    x = Activation('sigmoid')(x)
    x = Multiply()([x, input_tensor])

    return x

def ResNet18_10x10_Attention(input_shape=(10, 10, 1), num_classes=2):
    input_tensor = Input(shape=input_shape)

    x = Conv2D(filters=32, kernel_size=(3, 3), strides=(1, 1), padding='same', kernel_initializer=glorot_uniform())(input_tensor)
    x = Activation('relu')(x)
    x = MaxPooling2D(pool_size=(2, 2), strides=(2, 2), padding='same')(x)

    x = residual_block(x, filters=32)
    
    x = attention_block(x, filters=32)
    
    x = residual_block(x, filters=64, strides=(2, 2), downsample=True)
    
    x = attention_block(x, filters=64)
    
    x = residual_block(x, filters=128, strides=(2, 2), downsample=True)
    
    x = attention_block(x, filters=128)
    
    x = GlobalAveragePooling2D()(x)
    x = Dense(128, activation="relu")(x)
    x = Dropout(0.25)(x)
    x = Dense(256, activation="relu")(x)
    x = Dropout(0.25)(x)
    x = Dense(units=num_classes, activation='softmax')(x)

    model = Model(inputs=input_tensor, outputs=x, name='resnet18_10x10_attention')
    return model


model_10x10_attention = ResNet18_10x10_Attention(input_shape=(10, 10, 1), num_classes=2)

model_10x10_attention.summary()


optimizer = Adam(lr=0.001)

reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2,
                              patience=5, min_lr=0.00001)

checkpoint = ModelCheckpoint("best_model.h5", monitor='val_acc', verbose=1, save_best_only=True, mode='max')

callbacks = [reduce_lr, checkpoint]


model_10x10_attention.compile(optimizer = optimizer , loss = "binary_crossentropy", metrics=["accuracy"])


history = model_10x10_attention.fit(X_train, Y_train, epochs=20, batch_size=64, callbacks=callbacks, validation_data=(X_val, Y_val))
    
plt.plot(history.history['loss'], color='b', label="Train Loss")
plt.plot(history.history['val_loss'], color='r', label="Validation Loss")
plt.title(f"Train and Validation Loss (Dataset 1)",fontsize=15)
plt.xlabel("Epochs",fontsize=14)
plt.ylabel("Loss",fontsize=15)
plt.legend(loc='upper right',fontsize=13)
plt.xticks(fontsize=10)
plt.yticks(fontsize=10)
plt.show()


test_loss, test_acc = model_10x10_attention.evaluate(X_test, Y_test)
print(f"Test Loss: {test_loss}")
print(f"Test Accuracy: {test_acc}")

Y_pred = model_10x10_attention.predict(X_test)
Y_pred_classes = np.argmax(Y_pred, axis=1)
Y_true = np.argmax(Y_test, axis=1)


valid_loss, valid_acc = model_10x10_attention.evaluate(X_val, Y_val)
print(f"Valid Loss: {valid_loss}")
print(f"Valid Accuracy: {valid_acc}")
Y_predv = model_10x10_attention.predict(X_val)
Y_pred_classesv = np.argmax(Y_predv, axis=1)
Y_truev = np.argmax(Y_val, axis=1)

print("Confusion Matrix")
conf_matrix = confusion_matrix(Y_true, Y_pred_classes)
print(conf_matrix)

print("Classification Report Valid")
print(classification_report(Y_truev, Y_pred_classesv, digits=4))

print("Classification Report Test")
print(classification_report(Y_true, Y_pred_classes, digits=4))



plt.figure(figsize=(5, 5), dpi=100)
sns.heatmap(conf_matrix, annot=True, fmt="d", cmap="Blues", cbar=False, annot_kws={"size": 16})
plt.title("Confusion Matrix (Dataset 1)", fontsize=12)
plt.xlabel("Predicted Label", fontsize=12)
plt.ylabel("True Label", fontsize=12)
plt.xticks(fontsize=10)
plt.yticks(fontsize=10)
plt.show()

fpr, tpr, _ = roc_curve(Y_true, Y_pred[:, 1])
roc_auc = auc(fpr, tpr)

plt.figure(figsize=(8, 6))
plt.plot(fpr, tpr, color='darkorange', lw=2, label='ROC curve (area = %0.2f)' % roc_auc)
plt.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate',fontsize=15)
plt.ylabel('True Positive Rate',fontsize=15)
plt.title('Receiver Operating Characteristic (ROC) Curve (Dataset 1)',fontsize=17)
plt.legend(loc="lower right",fontsize=16)
plt.xticks(fontsize=12)
plt.yticks(fontsize=12)
plt.show()